# 变换
在本节中，将深入探讨 Relax 程序的变换。变换是编译流程中的关键组成部分，用于优化并与硬件后端进行集成。

首先，按照在 [上一节](relax-creation) 中所做的那样，创建简单的 Relax 程序。

In [1]:
import tvm
from tvm import IRModule, relax
from tvm.relax.frontend import nn


class NNModule(nn.Module):
    def __init__(self):
        super().__init__()
        self.fc1 = nn.Linear(784, 128)
        self.relu1 = nn.ReLU()
        self.fc2 = nn.Linear(128, 10)

    def forward(self, x):
        x = self.fc1(x)
        x = self.relu1(x)
        x = self.fc2(x)
        return x


origin_mod, params = NNModule().export_tvm(
    {"forward": {"x": nn.spec.Tensor(("n", 784), "float32")}}
)
origin_mod.show()

## 应用变换

Pass 是对程序应用变换的主要方式。可以对程序应用 Pass。作为第一步，让应用内置的 {py:class}`~tvm.relax.transform.LegalizeOps` Pass，将高级算子降级为低级算子。

In [2]:
mod = tvm.relax.transform.LegalizeOps()(origin_mod)
mod.show()

从输出可以看到，程序中的高级算子（即 ``relax.op``）已被相应的低级算子（即 ``relax.call_tir``）所取代。

接下来，尝试应用算子融合，这是机器学习编译器中广泛使用的一种优化技术。请注意，在 Relax 中，融合优化是通过一系列 Pass 的协作完成的。可以按顺序应用这些 Pass。

In [3]:
mod = tvm.ir.transform.Sequential(
    [
        tvm.relax.transform.AnnotateTIROpPattern(),
        tvm.relax.transform.FuseOps(),
        tvm.relax.transform.FuseTIR(),
    ]
)(mod)
mod.show()

结果显示，``matmul``、``add`` 和 ``relu`` 算子被融合到了内核中（即 ``call_tir``）。

有关所有内置 Pass 的详细信息，请参阅 {py:mod}`tvm.relax.transform`。

## 自定义 Pass

也可以定义自己的 Pass。以下是将 ``relu`` 算子重写为 ``gelu`` 算子的示例。

首先，需要编写 Relax IR Mutator 来执行重写。

In [4]:
from tvm.relax.expr_functor import PyExprMutator, mutator


@mutator
class ReluRewriter(PyExprMutator):
    def __init__(self, mod):
        super().__init__(mod)

    def visit_call_(self, call: relax.Call) -> relax.Expr:
        # visit the relax.Call expr, and only handle the case when op is relax.nn.relu
        if call.op.name == "relax.nn.relu":
            return relax.op.nn.gelu(call.args[0])

        return super().visit_call_(call)

然后，可以编写 Pass，将 Mutator 应用到整个模块中。

In [5]:
@tvm.transform.module_pass(opt_level=0, name="ReluToGelu")
class ReluToGelu:  # pylint: disable=too-few-public-methods
    def transform_module(self, mod: IRModule, _ctx: tvm.transform.PassContext) -> IRModule:
        """IRModule-level transformation"""
        rewriter = ReluRewriter(mod)
        for g_var, func in mod.functions_items():
            if isinstance(func, relax.Function):
                func = rewriter.visit_expr(func)
                rewriter.builder_.update_func(g_var, func)
        return rewriter.builder_.get()


mod = ReluToGelu()(origin_mod)
mod.show()

打印输出显示，``relax.nn.relu`` 运算符已被重写为 ``relax.nn.gelu`` 运算符。

有关 Mutator 的详细信息，请参阅 {py:class}`~tvm.relax.expr_functor.PyExprMutator`。

## 总结

在本节中，展示了如何对 Relax 程序应用转换。还展示了如何定义和应用自定义转换。